# COMP 579 - Assignment 3
[Ling Fei Zhang](https://github.com/Ling01234), 260985358

Sevag Baghdassarian, ID

Brandon Ma, ID

In [1]:
# imports
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt 
import gymnasium as gym
from tqdm import tqdm, trange
import random
import time
import matplotlib.colors as mcolors
from scipy.stats import sem
from sklearn.linear_model import LogisticRegression, LinearRegression
from sklearn.neural_network import MLPRegressor


# Q-Learning Agent

In [2]:
# Actions:
# 0: left
# 1: right

# best params initialization:
ALPHA = 1/4
EPSILON = 0.25
GAMMA = 0.95
BINS = 10
EPISODES = 1000
RUNS = 10
SEED = 123
random.seed(SEED)


class Qlearning:
    def __init__(self, env, alpha, gamma, epsilon, num_episodes, num_bins, seed) -> None:
        self.env = env
        self.alpha = alpha
        self.gamma = gamma
        self.epsilon = epsilon
        self.num_episodes = num_episodes
        self.num_bins = num_bins
        self.lowerbound = env.observation_space.low
        self.lowerbound[1] = -3.5
        self.lowerbound[3] = -10
        self.upperbound = env.observation_space.high
        self.upperbound[1] = 3.5
        self.upperbound[3] = 10
        # self.env.seed(seed)
        self.seed = seed
        random.seed(self.seed)
        self.num_action = env.action_space.n
        self.reward = []
        self.Qvalues = np.random.uniform(low=-0.001, high=0.001,
                                         size=(num_bins, num_bins, num_bins, num_bins, self.num_action))
        self.behavior_episodes1 = []
        self.behavior_episodes2 = []
        self.behavior_episodes3 = []
        self.random_episodes1 = []
        self.random_episodes2 = []
        self.random_episodes3 = []
        self.bins = []
        for i in range(4):
            self.bins.append(np.linspace(
                self.lowerbound[i], self.upperbound[i], self.num_bins))
            
    # def get_behavior_episodes(self):
    #     return np.apply_along_axis(np.argmax, 4, self.Qvalues) #shape (10, 10, 10, 10)
        

    def discritize_state(self, state):
        """
        Discritize continuous state into a discrete state

        Args:
            state (list of length 4): Current continuous state of agent

        Returns:
            state (4-tuple): Current discritized state of agent
        """
        new_state = []
        for i in range(4):
            index = np.maximum(np.digitize(state[i], self.bins[i]) - 1, 0)
            new_state.append(index)

        return tuple(new_state)

    def select_action(self, state, episode):
        """
        Select action given a state

        Args:
            state (4-tuple): Current state of the agent, continuous
            episode (int): Current episode of the run

        Returns:
            int: Action chosen by the agent
        """
        random.seed(self.seed)

        # lower exploration rate as we run many episodes
        if episode > 700:
            self.epsilon *= 0.99

        # epsilon greedy
        number = np.random.random()
        if number < self.epsilon:  # uniformly choose action
            return np.random.choice(self.num_action)

        # greedy selection
        state = self.discritize_state(state)
        best_actions = np.where(
            self.Qvalues[state] == np.max(self.Qvalues[state]))[0]
        return np.random.choice(best_actions)

    def simulate_episodes(self):
        """
        Simulate a specified number of episodes
        """
        for episode in range(1, self.num_episodes+1):
            # reset env
            (state, _) = self.env.reset()
            state = list(state)

            # run episode
            episode_reward = 0
            terminal = False
            while not terminal:
                discritized_state = self.discritize_state(state)
                action = self.select_action(state, episode)
                (next_state, reward, terminal, _, _) = self.env.step(action)
                episode_reward += reward

                next_discritized_state = self.discritize_state(
                    list(next_state))

                q_max = np.max(self.Qvalues[next_discritized_state])
                self.qlearning_update(
                    terminal, reward, action, discritized_state, q_max)

                state = next_state

            self.reward.append(int(episode_reward))

    def qlearning_update(self, terminal, reward, action, state, q_max):
        """
        Qlearning update rule

        Args:
            terminal (bool): True if at terminal state, False otherwise
            reward (int): Reward of the agent at current state
            action (int): Action taken by agent
            state (4-tuple): Discrete state of the agent
            q_max (float): Max Q value of the next state
        """
        if not terminal:
            loss = reward + self.gamma * q_max - \
                self.Qvalues[state + (action,)]
        else:
            loss = reward - self.Qvalues[state + (action,)]

        self.Qvalues[state + (action,)] += self.alpha * loss

    def visualize(self, games):
        """
        Visualize the game played for a specified number of games.
        Prints out the reward for each game.

        Args:
            games (int): Number of games to be played
        """
        random.seed(self.seed)
        env = gym.make("CartPole-v1", render_mode="human")
        for game in range(games):
            (state, _) = env.reset()
            env.render()
            rewards = 0

            for _ in range(500):
                discritized_state = self.discritize_state(state)
                best_actions = np.where(self.Qvalues[discritized_state] == np.max(
                    self.Qvalues[discritized_state]))[0]
                action = np.random.choice(best_actions)
                (state, reward, terminal, _, _) = env.step(action)
                rewards += int(reward)
                time.sleep(0.05)

                if terminal:
                    time.sleep(1)
                    break
            print(f"reward for game {game}: {rewards}")
        env.close()
        
    def gather_episodes_agent(self, num_episodes):
        """
        Gather num_episodes behavior episodes for simple imitation learning

        Args:
            num_episodes (int): number of behavior episodes desired

        Returns:
            int: return of simple imitation learning using Q-Learning Agent
            as expert.
        """
        self.simulate_episodes()
        print(f"reward after simulate_episode: {self.reward[-20:]}")
        for episode in trange(1, num_episodes+1):
            # if episode % 10 == 0:
            #     print(f"gather episode {episode}")
            state, _ = self.env.reset()
            terminal = False
            while not terminal:
                discritized_state = self.discritize_state(state)
                best_actions = np.where(self.Qvalues[discritized_state] == np.max(
                    self.Qvalues[discritized_state]))[0]
                action = np.random.choice(best_actions)
                (next_state, reward, terminal, _, _) = self.env.step(action)
                discritized_next_state = self.discritize_state(next_state)
                
                if episode <= 100:
                    self.behavior_episodes1.append((discritized_state, action, reward, discritized_next_state, terminal))
                    self.behavior_episodes2.append((discritized_state, action, reward, discritized_next_state, terminal))
                if episode <= 250:
                    self.behavior_episodes2.append((discritized_state, action, reward, discritized_next_state, terminal))
                self.behavior_episodes3.append((discritized_state, action, reward, discritized_next_state, terminal))
                
                state = next_state
                
        # preprocess data
        x = np.array([data[0] for data in self.behavior_episodes3])
        y = np.array([data[1] for data in self.behavior_episodes3])
                
        episode_reward = self.simple_imitation(x, y)
        return episode_reward
        
        

    
    def gather_episodes_random(self, num_episodes):
        """
        Gather num_episodes behavior episodes with a random agent

        Args:
            num_episodes (int): number of behavior episodes desired for simple imitation

        Returns:
            int: return by a random agent. 
        """
        # print(f"reward after simulate_episode: {self.reward[-20:]}")
        for episode in trange(1, num_episodes+1):
            # if episode % 10 == 0:
            #     print(f"random agent episode {episode}")
            state, _ = self.env.reset()
            terminal = False
            while not terminal:
                discritized_state = self.discritize_state(state)
                action = self.env.action_space.sample()
                (next_state, reward, terminal, _, _) = self.env.step(action)
                discritized_next_state = self.discritize_state(next_state)
                
                if episode <= 100:
                    self.random_episodes1.append((discritized_state, action, reward, discritized_next_state, terminal))
                    self.random_episodes2.append((discritized_state, action, reward, discritized_next_state, terminal))
                if episode <= 250:
                    self.random_episodes2.append((discritized_state, action, reward, discritized_next_state, terminal))
                self.random_episodes3.append((discritized_state, action, reward, discritized_next_state, terminal))
                
                state = next_state
                
        # preprocess data
        x = np.array([data[0] for data in self.random_episodes3])
        y = np.array([data[1] for data in self.random_episodes3])
        
        episode_reward = self.simple_imitation(x, y)
        return episode_reward
        

    def simple_imitation(self, x, y):
        """
        Simple imitation estimator

        Args:
            x (list): list of states from dataset
            y (list): list of actions from dataset

        Returns:
            int: return observed by the agent during testing
        """
        model = LogisticRegression()
        model.fit(x, y)
        
        state, _ = self.env.reset()
        episode_reward = 0
        terminal = False
        while not terminal:
            state = np.array(self.discritize_state(state))
            action = model.predict(state.reshape(1, -1))[0]
            state, reward, terminal, *_ = self.env.step(action)
            episode_reward += reward
        return episode_reward


Here, we will run a test run on the model, and see how it performs

In [3]:
def test_model():
    env = gym.make("CartPole-v1")
    qlearning = Qlearning(env, ALPHA, GAMMA, EPSILON, EPISODES, BINS, SEED)
    model_rewards = qlearning.gather_episodes_agent(500)
    random_rewards = qlearning.gather_episodes_random(500)
    print(f"Simple imitation with expert agent reward: {model_rewards}")
    print(f"Simple imitation with random agent reward: {random_rewards}")
    env.close()
    return qlearning.behavior_episodes1, qlearning.random_episodes1, qlearning.behavior_episodes2, qlearning.random_episodes2, qlearning.behavior_episodes3, qlearning.random_episodes3
    
data1, data2, data3, data4, data5, data6 = test_model()    

reward after simulate_episode: [146, 237, 225, 212, 255, 278, 360, 199, 226, 225, 365, 270, 180, 205, 232, 268, 207, 306, 246, 300]


100%|██████████| 500/500 [00:00<00:00, 1102.32it/s]

Simple imitation with expert agent reward: 180.0
Simple imitation with random agent reward: 30.0


We have pre-trained our Q-Learning agent with 1000 episodes, as we did in the previous assignment. We then use the trained Q-Learning agent as our expert in simple imitation learning and used logisitc regression to imitate the action observed in each state. The results above were produced using 500 behavior episodes. We can see that we can get decent results from simple imitation learning. On the other hand, we can see the returns received by the random agent. Without surprise, the returns are very low. 

# Datasets
Below, we will create the 9 datasets we need to perform our analysis. 

In [4]:
# expert Q-learning data
# 100 episodes of expert data
x1 = np.array([data[0] for data in data1])
y1 = np.array([data[1] for data in data1])

# 250 episodes of expert data
x3 = np.array([data[0] for data in data3])
y3 = np.array([data[1] for data in data3])

# 500 episodes of expert data
x5 = np.array([data[0] for data in data5])
y5 = np.array([data[1] for data in data5])



# random agent data
# 100 episodes of random data
x2 = np.array([data[0] for data in data2])
y2 = np.array([data[1] for data in data2])

# 250 episodes of random data
x4 = np.array([data[0] for data in data4])
y4 = np.array([data[1] for data in data4])

# 500 episodes of random data
x6 = np.array([data[0] for data in data6])
y6 = np.array([data[1] for data in data6])

# Shuffled data
shuffled_data = data5 + data6
random.shuffle(shuffled_data)

# 100 episodes of mixed data
data7 = shuffled_data[:int(len(shuffled_data)/10)]
x7 = np.array([data[0] for data in data7])
y7 = np.array([data[1] for data in data7])

# 250 episodes of mixed data
data8 = shuffled_data[:int(len(shuffled_data)/4)]
x8 = np.array([data[0] for data in data8])
y8 = np.array([data[1] for data in data8])

# 500 episodes of mixed data
data9 = shuffled_data[:int(len(shuffled_data)/2)]
x9 = np.array([data[0] for data in data9])
y9 = np.array([data[1] for data in data9])


# Fitted Q-Learning

In [18]:
class FittedQLearning:
    def __init__(self, env, buffer, gamma=0.99, num_episodes=500, batch_size=64, buffer_size=5000, approximator="linear"):
        self.env = env
        self.gamma = gamma
        self.num_episodes = num_episodes
        self.batch_size = batch_size
        self.buffer_size = buffer_size
        self.buffer = buffer
        self.state_space = env.observation_space.shape[0]
        self.action_space = env.action_space.n
        self.approximator = approximator

        # build model
        if approximator == "linear":
            self.model = LinearRegression()
        elif approximator == "mlp":
            self.model = MLPRegressor(hidden_layer_sizes=(
                64,), activation="relu", solver="adam", max_iter=1000)
        else:
            raise Exception("The approximator must be 'linear' or 'mlp'")

        # initial fit of the approximator
        self.initial_fit()

        # initial buffer
        for data in self.buffer[:self.buffer_size]:
            self.remember(*data)

    def initial_fit(self):
        if self.approximator == "linear":
            weights = np.random.uniform(low=-0.001, high=0.001,
                                        size=(1, self.state_space + 1))
            weights_inter = np.random.uniform(low=-0.001, high=0.001,
                                        size=(1,))
            
            self.model.coef_ = weights
            self.model.intercept_ = weights_inter

        else: # TO MODIFY WITH PROPER SIZE
            layer_sizes = self.model.hidden_layer_sizes + (1,)
            weights = []
            for i in range(len(layer_sizes) - 1):
                w = [np.random.uniform(low=-0.001, high=0.001,
                                       size=(layer_sizes[i], layer_sizes[i+1]))]
                weights.append(w)
            self.model.coefs_ = weights
        # self.model.fit(self.buffer[:, :4], self.buffer[:, 4])

    def predict(self, state):
        # qvalue = self.model.predict(np.array(state).reshape(1, -1))[0]
        action0 = np.array(0)
        action1 = np.array(1)
        qvalue1 = self.model.predict(np.hstack((state, action0)).reshape(1,-1))[0][0]
        qvalue2 = self.model.predict(np.hstack((state, action1)).reshape(1,-1))[0][0]
        qvalues = [qvalue1, qvalue2]
        print(f"qvalue in predict: {qvalues}")
        return qvalues

    def update(self):
        if len(self.buffer) > self.batch_size:
            batch_index = np.random.choice(
                len(self.buffer), size=self.batch_size)
            batch = [self.buffer[i] for i in batch_index]
            states, actions, rewards, next_states, dones = zip(*batch)
            
            # batch training
            # X = []
            # y = []
            for index in range(self.batch_size): 
                print(f"index: {index}")
                if dones[index] == True:
                    max_qvalue = 0
                else:
                    qvalues = self.predict(next_states[index])
                    max_qvalue = np.max(qvalues)
                
                target = rewards[index] + self.gamma * max_qvalue
                target = np.array(target).reshape(-1,1)
                x = np.hstack((states[index], actions[index])).reshape(1,-1)
                # X.append(x)
                # y.append(target)
                print(f"x: {x}")
                print(f"target: {target}")
                self.model.fit(x,target)
                
                # current_qvalue = self.model.predict(x)
                # print(f"current q value: {current_qvalue}")
                # error = current_qvalue[0][0] - target[0][0]
                # gradient = np.dot(np.hstack((next_states[index], actions[index])).reshape(1,-1), error)
                # print(f"gradient: {gradient}")
                # self.model.coef_ -= 0.01 * gradient
                # self.model.intercept_ -= 0.01 * error
                
            
            
            
            
            # states = np.array(states)
            # actions = np.array(actions)
            # rewards = np.array(rewards)
            # next_states = np.array(next_states)
            # dones = np.array([int(done) for done in dones])

            # # axis 1 checks for each next_state
            # next_qvalues = []
            # for index, next_state in enumerate(next_states):
            #     # print(f"in enumerate: {index}")
            #     if dones[index] == 1:
            #         qvalue = 0
            #     else:
            #         # print(f"in else")
            #         qvalue = self.predict(next_state)
            #         qvalue = np.max(qvalue)
            #     next_qvalues.append(qvalue)
            # next_qvalues = np.array(next_qvalues)
            # print(f"next_qvalues in update: {next_qvalues}")
            # target_qvalues = rewards + self.gamma * (1 - dones) * next_qvalues

            # if self.approximator == "linear":
            #     x = np.hstack((states, actions.reshape(-1, 1)))
            #     # x = states
            # else:
            #     x = states
            # y = target_qvalues.reshape(-1, 1)

            # self.model.fit(x, y)

    def select_action(self, state):
        qvalues = self.predict(state)
        action = np.argmax(qvalues)
        print(f"action in select_action: {action}")
        return action

    def remember(self, state, action, reward, next_state, done):
        if len(self.buffer) > self.buffer_size:
            self.buffer.pop(0)
        self.buffer.append((state, action, reward, next_state, done))

    def train(self):
        for episode in trange(1, self.num_episodes+1):
            state, _ = self.env.reset()
            done = False
            while not done:
                action = self.select_action(state)
                next_state, reward, done, *_ = self.env.step(action)
                self.remember(state, action, reward, next_state, done)
                state = next_state

            self.update()

            # if episode % 10 == 0:
            #     print(f"episode {episode} in training")

    def test(self):
        state, _ = self.env.reset()
        episode_reward = 0
        done = False
        while not done:
            action = self.select_action(state)
            state, reward, done, *_ = self.env.step(action)
            episode_reward += reward

        return episode_reward
                    
def test_model_fitted():
    env = gym.make("CartPole-v1")
    model = FittedQLearning(env, data5)
    model.train()
    reward = model.test()
    print(f"testing reward: {reward}")
    env.close()
    
test_model_fitted()

            

  1%|▏         | 7/500 [00:00<00:16, 30.45it/s]

qvalue in predict: [-6.637934441687545e-05, 0.000905276997435889]
action in select_action: 1
qvalue in predict: [-2.5592246286705855e-05, 0.0009460640955660586]
action in select_action: 1
qvalue in predict: [2.0368090681963883e-05, 0.0009920244325347283]
action in select_action: 1
qvalue in predict: [7.10535973826892e-05, 0.0010427099392354535]
action in select_action: 1
qvalue in predict: [0.00012604913849003594, 0.0010977054803428003]
action in select_action: 1
qvalue in predict: [0.0001849748253427273, 0.0011566311671954918]
action in select_action: 1
qvalue in predict: [0.00024748873646525654, 0.001219145078318021]
action in select_action: 1
qvalue in predict: [0.00031329003194161497, 0.0012849463737943795]
action in select_action: 1
qvalue in predict: [0.00038212314822941426, 0.0013537794900821787]
action in select_action: 1
qvalue in predict: [0.0004537823357328903, 0.001425438677585655]
action in select_action: 1
index: 0
qvalue in predict: [0.0012548666618182806, 0.002226523003

  2%|▏         | 11/500 [00:00<00:15, 30.79it/s]

qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
action in select_action: 0
index: 0
qvalue in predict: [57.011098647610595, 57.011098647610595]
x: [[4 3 3 4 0]]
target: [[57.44098766]]
index: 1
qvalue in predict: [57.440987661134486, 57.440987661134486]
x: [[3 2 3 4 0]]
target: [[57.86657778

  4%|▍         | 19/500 [00:00<00:15, 31.86it/s]

...

index: 15
qvalue in predict: [58.28791200667791, 58.28791200667791]
x: [[2 1 5 5 0]]
target: [[58.70503289]]
index: 16
qvalue in predict: [58.70503288661113, 58.70503288661113]
x: [[4 5 5 4 1]]
target: [[59.11798256]]
index: 17
qvalue in predict: [59.117982557745016, 59.117982557745016]
x: [[3 2 4 4 1]]
target: [[59.52680273]]
index: 18
qvalue in predict: [59.52680273216757, 59.52680273216757]
x: [[-0.05295809 -0.80916131  0.07312692  1.25924349  0.        ]]
target: [[59.9315347]]
index: 19
qvalue in predict: [59.931534704845895, 59.931534704845895]
x: [[4 3 4 4 1]]
target: [[60.33221936]]
index: 20
qvalue in predict: [60.332219357797435, 60.332219357797435]
x: [[-0.04547072 -0.82837373  0.07240784  1.2499603   0.        ]]
target: [[60.72889716]]
index: 21
qvalue in predict: [60.72889716421946, 60.72889716421946]
x: [[ 0.02341231 -0.79464447  0.02992742  1.21703303  0.        ]]
target: [[61.12160819]]
index: 22
qvalue in predict: [61.12160819257726, 61.12160819257726]
x: [[3 3 4 4 1

 98%|█████████▊| 491/500 [00:15<00:00, 30.94it/s]

qvalue in predict: [45.284335760923845, 45.284335760923845]
x: [[-0.02247927 -0.61282122  0.05925548  0.96046793  0.        ]]
target: [[45.8314924]]
index: 53
qvalue in predict: [45.831492403314606, 45.831492403314606]
x: [[3 4 3 4 0]]
target: [[46.37317748]]
index: 54
qvalue in predict: [46.37317747928146, 46.37317747928146]
x: [[4 3 4 4 1]]
target: [[46.9094457]]
index: 55
qvalue in predict: [46.90944570448865, 46.90944570448865]
x: [[ 0.01105329  0.42822474 -0.01667406 -0.5986712   1.        ]]
target: [[47.44035125]]
index: 56
qvalue in predict: [47.44035124744376, 47.44035124744376]
x: [[4 4 4 4 0]]
target: [[47.96594773]]
index: 57
qvalue in predict: [47.96594773496932, 47.96594773496932]
x: [[4 4 3 4 0]]
target: [[48.48628826]]
index: 58
qvalue in predict: [48.48628825761963, 48.48628825761963]
x: [[4 4 3 4 0]]
target: [[49.00142538]]
index: 59
qvalue in predict: [49.00142537504343, 49.00142537504343]
x: [[4 4 3 4 0]]
target: [[49.51141112]]
index: 60
qvalue in predict: [49.511

100%|██████████| 500/500 [00:15<00:00, 31.32it/s]

index: 8
qvalue in predict: [28.944677272770754, 28.944677272770754]
x: [[ 0.05356637  0.42057726 -0.04653993 -0.63338995  1.        ]]
target: [[29.6552305]]
index: 9
qvalue in predict: [29.655230500043047, 29.655230500043047]
x: [[4 3 4 4 1]]
target: [[30.3586782]]
index: 10
qvalue in predict: [30.358678195042614, 30.358678195042614]
x: [[ 0.05909278  1.39281976 -0.15015736 -2.17906165  1.        ]]
target: [[31.05509141]]
index: 11
qvalue in predict: [31.05509141309219, 31.05509141309219]
x: [[4 4 3 4 0]]
target: [[31.7445405]]
index: 12
qvalue in predict: [31.744540498961268, 31.744540498961268]
x: [[3 2 4 4 1]]
target: [[32.42709509]]
index: 13
qvalue in predict: [32.42709509397166, 32.42709509397166]
x: [[-0.01387351 -0.62521774  0.01058758  0.87808836  0.        ]]
target: [[33.10282414]]
index: 14
qvalue in predict: [33.10282414303194, 33.10282414303194]
x: [[4 4 5 4 1]]
target: [[33.7717959]]
index: 15
qvalue in predict: [33.77179590160162, 33.77179590160162]
x: [[4 5 4 4 1]]
